In [1]:
# force to use cpu
import os
os.environ["CUDA_VISIBLE_DEVICES"]="-1"

import numpy as np
import pandas as pd
from pandas import read_csv
from keras.models import Sequential
from keras.layers import Dense, Dropout
from sklearn.preprocessing import MinMaxScaler

import matplotlib.pyplot as plt
%matplotlib inline

def create_dataset(signal_data, look_back=1):
    dataX, dataY = [], []
    for i in range(len(signal_data)-look_back):
        dataX.append(signal_data[i:(i+look_back), 0]) 
        dataY.append(signal_data[i + look_back, 0]) 
    return np.array(dataX), np.array(dataY)

look_back =  1440 # 1440 min = 1 day

Using TensorFlow backend.


In [2]:
# load apm cpu for specific mid  ex:288
apm_cpu_data = read_csv("dataset/1808-12.csv", index_col="logtime")
apm_cpu_data = apm_cpu_data[apm_cpu_data['mid'] == 288]
apm_cpu_data = apm_cpu_data.drop(columns='mid')
apm_cpu_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 201446 entries, 2018-08-01T15:29:07 to 2018-12-24T15:32:51
Data columns (total 1 columns):
cpu.usage    201446 non-null float64
dtypes: float64(1)
memory usage: 3.1+ MB


In [3]:
# extract cpu.usage from apm data
values = apm_cpu_data['cpu.usage'].values
values = values.reshape(-1, 1)
values.astype('float32')

# pre-process data
scaler = MinMaxScaler(feature_range=(0, 1))
signal_data = scaler.fit_transform(values)

# split data
train = values[0:len(values)//2]   # 50%
val = values[len(train):(len(train)+len(apm_cpu_data)//4)]  # 25%
test = values[(len(train)+len(val)):]    # 25%

In [4]:
# gen dataset
x_train, y_train = create_dataset(train, look_back)
x_val, y_val = create_dataset(val, look_back)
x_test, y_test = create_dataset(test, look_back)

In [5]:
# pre-process dataset
x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))
x_val = np.reshape(x_val, (x_val.shape[0], x_val.shape[1], 1))
x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))

x_train = np.squeeze(x_train)
x_val = np.squeeze(x_val)
x_test = np.squeeze(x_test)

In [6]:
# generate train model
model = Sequential()
model.add(Dense(32,input_dim=1440,activation="relu"))
for i in range(5):
    model.add(Dense(32,activation="relu"))
model.add(Dense(1))

In [7]:
#  set train setting
model.compile(loss='mae', optimizer='adam', metrics=['acc'])

In [8]:
# train model
from keras.callbacks import EarlyStopping
early_stopping = EarlyStopping(patience = 30) 
hist = model.fit(x_train, y_train, epochs=100, batch_size=10, 
                 validation_data=(x_val, y_val), callbacks=[early_stopping], verbose=1)

Train on 99283 samples, validate on 48921 samples
Epoch 1/100
99283/99283 [==============================] - 22s 217us/step - loss: 0.6997 - acc: 0.6039 - val_loss: 0.6813 - val_acc: 0.6978
Epoch 2/100
99283/99283 [==============================] - 22s 217us/step - loss: 0.6110 - acc: 0.6556 - val_loss: 0.6501 - val_acc: 0.6989
Epoch 3/100
99283/99283 [==============================] - 22s 217us/step - loss: 0.5780 - acc: 0.6706 - val_loss: 0.6723 - val_acc: 0.6689
Epoch 4/100
99283/99283 [==============================] - 21s 214us/step - loss: 0.5623 - acc: 0.6779 - val_loss: 0.6374 - val_acc: 0.7019
Epoch 5/100
99283/99283 [==============================] - 21s 214us/step - loss: 0.5535 - acc: 0.6816 - val_loss: 0.6189 - val_acc: 0.7132
Epoch 6/100
99283/99283 [==============================] - 21s 213us/step - loss: 0.5488 - acc: 0.6827 - val_loss: 0.6846 - val_acc: 0.6649
Epoch 7/100
99283/99283 [==============================] - 20s 205us/step - loss: 0.5420 - acc: 0.6860 - val_l

Epoch 59/100
99283/99283 [==============================] - 21s 213us/step - loss: 0.4727 - acc: 0.6965 - val_loss: 0.5501 - val_acc: 0.7207
Epoch 60/100
99283/99283 [==============================] - 21s 212us/step - loss: 0.4714 - acc: 0.6978 - val_loss: 0.6136 - val_acc: 0.6752
Epoch 61/100
99283/99283 [==============================] - 21s 207us/step - loss: 0.4727 - acc: 0.6966 - val_loss: 0.5727 - val_acc: 0.7046
Epoch 62/100
99283/99283 [==============================] - 21s 210us/step - loss: 0.4777 - acc: 0.6939 - val_loss: 0.5794 - val_acc: 0.7242
Epoch 63/100
99283/99283 [==============================] - 21s 212us/step - loss: 0.4698 - acc: 0.6999 - val_loss: 0.5581 - val_acc: 0.7136
Epoch 64/100
99283/99283 [==============================] - 21s 211us/step - loss: 0.4797 - acc: 0.6908 - val_loss: 0.6195 - val_acc: 0.6435
Epoch 65/100
99283/99283 [==============================] - 21s 209us/step - loss: 0.4702 - acc: 0.6979 - val_loss: 0.5501 - val_acc: 0.7229
Epoch 66/100


In [9]:
# evulate model
trainScore = model.evaluate(x_train, y_train, verbose=0)
print('Train Score: ', trainScore)
valScore = model.evaluate(x_val, y_val, verbose=0)
print('Validataion Score: ', valScore)
testScore = model.evaluate(x_test, y_test, verbose=0)
print('Test Score: ', testScore)

Train Score:  [0.47272565858756893, 0.6944592729915215]
Validataion Score:  [0.573053915328885, 0.7152347662533634]
Test Score:  [0.748655497546549, 0.680532275875018]


In [10]:
# save model with weight and bias
model.save("mlp_mae-adam_final.h5")

In [11]:
# use model to predict
yhat = model.predict(x_test)

In [12]:
# translate x-axis data to real date format with KST timezone(+09:00)
predictDates = apm_cpu_data.tail(len(x_test)).index
kstDates = pd.to_datetime(predictDates) + pd.DateOffset(hours=9)

In [15]:
j = 0
for i in kstDates:
    act = y_test[j]
    pred = round(yhat[j][0], 2)
    diff = round(yhat[j][0] - y_test[j], 2)
    
    if pred < 0:
        pred = 0
    elif pred == 0:
        pred = 0
    
    if diff > 0:
        pm = 1
    elif diff == 0:
        pm = 0
    elif diff < 0:
        pm = -1
    
    
    if act <=  0:
        act = -1
        print ("[XXX] => %s : cpu usage data wasn't collected\n" % i)
    else:
        print ("Time : %s" % i)
        print ("Actual : %s  |  Predict : %s  |  diff : %s  |  pm : %s\n" % (act, pred, diff, pm) )
    
    j += 1

Time : 2018-11-19 08:46:06
Actual : 25.0  |  Predict : 10.4  |  diff : -14.6  |  pm : -1

Time : 2018-11-19 08:47:06
Actual : 28.0  |  Predict : 17.59  |  diff : -10.41  |  pm : -1

Time : 2018-11-19 08:48:06
Actual : 25.0  |  Predict : 0  |  diff : -25.0  |  pm : -1

Time : 2018-11-19 08:49:06
Actual : 25.0  |  Predict : 1.0  |  diff : -24.0  |  pm : -1

Time : 2018-11-19 08:50:06
Actual : 24.0  |  Predict : 0.01  |  diff : -23.99  |  pm : -1

Time : 2018-11-19 08:51:06
Actual : 21.0  |  Predict : 0  |  diff : -21.0  |  pm : -1

Time : 2018-11-19 08:52:06
Actual : 3.0  |  Predict : 2.1  |  diff : -0.9  |  pm : -1

[XXX] => 2018-11-19 08:53:07 : cpu usage data wasn't collected

Time : 2018-11-19 08:54:06
Actual : 1.0  |  Predict : 2.04  |  diff : 1.04  |  pm : 1

[XXX] => 2018-11-19 08:55:06 : cpu usage data wasn't collected

[XXX] => 2018-11-19 08:56:06 : cpu usage data wasn't collected

Time : 2018-11-19 08:57:06
Actual : 4.0  |  Predict : 1.0  |  diff : -3.0  |  pm : -1

Time : 2018


Time : 2018-11-20 12:01:27
Actual : 1.0  |  Predict : 0.01  |  diff : -0.99  |  pm : -1

Time : 2018-11-20 12:02:27
Actual : 2.0  |  Predict : 1.97  |  diff : -0.03  |  pm : -1

Time : 2018-11-20 12:03:27
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-20 12:04:27 : cpu usage data wasn't collected

Time : 2018-11-20 12:05:27
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-20 12:06:27 : cpu usage data wasn't collected

Time : 2018-11-20 12:07:27
Actual : 2.0  |  Predict : 2.0  |  diff : 0.0  |  pm : 0

Time : 2018-11-20 12:08:27
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-20 12:09:28 : cpu usage data wasn't collected

Time : 2018-11-20 12:10:27
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-20 12:11:27 : cpu usage data wasn't collected

Time : 2018-11-20 12:12:27
Actual : 3.0  |  Predict : 2.73  |  diff : -0.27  |  pm : -1

Time : 2018-11-20 12:13:27
Actual : 6.0  |  Predict

Time : 2018-11-21 14:00:36
Actual : 6.0  |  Predict : 6.14  |  diff : 0.14  |  pm : 1

[XXX] => 2018-11-21 14:01:36 : cpu usage data wasn't collected

Time : 2018-11-21 14:02:36
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm : 0

Time : 2018-11-21 14:03:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-21 14:04:36 : cpu usage data wasn't collected

Time : 2018-11-21 14:05:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-11-21 14:06:36
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

Time : 2018-11-21 14:07:36
Actual : 9.0  |  Predict : 2.86  |  diff : -6.14  |  pm : -1

Time : 2018-11-21 14:08:37
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-11-21 14:09:36
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

Time : 2018-11-21 14:10:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-21 14:11:36 : cpu usage data wasn't collected

Time : 2018-11-21 14:12:36
Actual : 

Time : 2018-11-22 16:03:46
Actual : 6.0  |  Predict : 6.1  |  diff : 0.1  |  pm : 1

[XXX] => 2018-11-22 16:04:46 : cpu usage data wasn't collected

Time : 2018-11-22 16:05:46
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-22 16:06:46 : cpu usage data wasn't collected

Time : 2018-11-22 16:07:46
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm : 0

Time : 2018-11-22 16:08:46
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-22 16:09:46 : cpu usage data wasn't collected

Time : 2018-11-22 16:10:46
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-22 16:11:46 : cpu usage data wasn't collected

Time : 2018-11-22 16:12:46
Actual : 3.0  |  Predict : 4.5  |  diff : 1.5  |  pm : 1

[XXX] => 2018-11-22 16:13:46 : cpu usage data wasn't collected

[XXX] => 2018-11-22 16:14:46 : cpu usage data wasn't collected

Time : 2018-11-22 16:15:46
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-22 

Actual : 2.0  |  Predict : 2.01  |  diff : 0.01  |  pm : 1

Time : 2018-11-23 18:03:41
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-23 18:04:41 : cpu usage data wasn't collected

Time : 2018-11-23 18:05:41
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-11-23 18:06:41
Actual : 5.0  |  Predict : 6.3  |  diff : 1.3  |  pm : 1

Time : 2018-11-23 18:07:41
Actual : 2.0  |  Predict : 4.07  |  diff : 2.07  |  pm : 1

Time : 2018-11-23 18:08:41
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-23 18:09:41 : cpu usage data wasn't collected

Time : 2018-11-23 18:10:41
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-11-23 18:11:41 : cpu usage data wasn't collected

Time : 2018-11-23 18:12:41
Actual : 2.0  |  Predict : 3.04  |  diff : 1.04  |  pm : 1

Time : 2018-11-23 18:13:41
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

[XXX] => 2018-11-23 18:14:41 : cpu usage data wasn't collected



...

Time : 2018-12-20 07:23:43
Actual : 6.0  |  Predict : 5.36  |  diff : -0.64  |  pm : -1

Time : 2018-12-20 07:24:43
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm : 0

Time : 2018-12-20 07:25:43
Actual : 1.0  |  Predict : 0.2  |  diff : -0.8  |  pm : -1

Time : 2018-12-20 07:26:43
Actual : 3.0  |  Predict : 3.0  |  diff : -0.0  |  pm : 0

[XXX] => 2018-12-20 07:27:43 : cpu usage data wasn't collected

Time : 2018-12-20 07:28:43
Actual : 1.0  |  Predict : 0.01  |  diff : -0.99  |  pm : -1

Time : 2018-12-20 07:29:43
Actual : 1.0  |  Predict : 0.2  |  diff : -0.8  |  pm : -1

[XXX] => 2018-12-20 07:30:43 : cpu usage data wasn't collected

Time : 2018-12-20 07:31:43
Actual : 3.0  |  Predict : 2.9  |  diff : -0.1  |  pm : -1

[XXX] => 2018-12-20 07:32:43 : cpu usage data wasn't collected

Time : 2018-12-20 07:33:43
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-20 07:34:43
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

[XXX] => 2018-12-20 07:35:4

Time : 2018-12-21 08:06:36
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm : 0

Time : 2018-12-21 08:07:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-21 08:08:36 : cpu usage data wasn't collected

Time : 2018-12-21 08:09:36
Actual : 1.0  |  Predict : 0.01  |  diff : -0.99  |  pm : -1

Time : 2018-12-21 08:10:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-21 08:11:36
Actual : 1.0  |  Predict : 2.0  |  diff : 1.0  |  pm : 1

Time : 2018-12-21 08:12:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-21 08:13:36 : cpu usage data wasn't collected

Time : 2018-12-21 08:14:36
Actual : 2.0  |  Predict : 1.0  |  diff : -1.0  |  pm : -1

[XXX] => 2018-12-21 08:15:36 : cpu usage data wasn't collected

Time : 2018-12-21 08:16:36
Actual : 2.0  |  Predict : 2.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-21 08:17:36
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-21 08:18:36
Actual : 


[XXX] => 2018-12-22 09:29:39 : cpu usage data wasn't collected

[XXX] => 2018-12-22 09:30:39 : cpu usage data wasn't collected

Time : 2018-12-22 09:31:39
Actual : 8.0  |  Predict : 7.09  |  diff : -0.91  |  pm : -1

[XXX] => 2018-12-22 09:32:39 : cpu usage data wasn't collected

Time : 2018-12-22 09:33:40
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-22 09:34:40
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

Time : 2018-12-22 09:35:41
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

Time : 2018-12-22 09:36:41
Actual : 2.0  |  Predict : 2.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-22 09:37:41 : cpu usage data wasn't collected

Time : 2018-12-22 09:38:41
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-22 09:39:41 : cpu usage data wasn't collected

Time : 2018-12-22 09:40:41
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-22 09:41:41
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm

Time : 2018-12-23 12:27:42
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-23 12:28:42 : cpu usage data wasn't collected

Time : 2018-12-23 12:29:42
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-23 12:30:42 : cpu usage data wasn't collected

Time : 2018-12-23 12:31:42
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm : 0

Time : 2018-12-23 12:32:42
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-23 12:33:42 : cpu usage data wasn't collected

Time : 2018-12-23 12:34:42
Actual : 2.0  |  Predict : 2.0  |  diff : -0.0  |  pm : 0

[XXX] => 2018-12-23 12:35:42 : cpu usage data wasn't collected

Time : 2018-12-23 12:36:42
Actual : 3.0  |  Predict : 2.91  |  diff : -0.09  |  pm : -1

Time : 2018-12-23 12:37:42
Actual : 1.0  |  Predict : 0  |  diff : -1.0  |  pm : -1

[XXX] => 2018-12-23 12:38:42 : cpu usage data wasn't collected

Time : 2018-12-23 12:39:42
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm

Time : 2018-12-24 11:19:51
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-24 11:20:51 : cpu usage data wasn't collected

Time : 2018-12-24 11:21:51
Actual : 2.0  |  Predict : 2.0  |  diff : 0.0  |  pm : 0

Time : 2018-12-24 11:22:51
Actual : 6.0  |  Predict : 6.18  |  diff : 0.18  |  pm : 1

[XXX] => 2018-12-24 11:23:51 : cpu usage data wasn't collected

Time : 2018-12-24 11:24:51
Actual : 2.0  |  Predict : 2.01  |  diff : 0.01  |  pm : 1

[XXX] => 2018-12-24 11:25:51 : cpu usage data wasn't collected

Time : 2018-12-24 11:26:51
Actual : 3.0  |  Predict : 2.94  |  diff : -0.06  |  pm : -1

[XXX] => 2018-12-24 11:27:51 : cpu usage data wasn't collected

[XXX] => 2018-12-24 11:28:51 : cpu usage data wasn't collected

Time : 2018-12-24 11:29:51
Actual : 1.0  |  Predict : 1.0  |  diff : 0.0  |  pm : 0

[XXX] => 2018-12-24 11:30:51 : cpu usage data wasn't collected

Time : 2018-12-24 11:31:51
Actual : 3.0  |  Predict : 3.02  |  diff : 0.02  |  pm : 1

[XXX] => 20